# Alimentador obra - símbolos

Notebook para crear los símbolos y vincularlos a las obras.  Necesita dos tablas. Una que contiene los ids de las obras a crear y otra que contiene la relación de los símbolos y obras del excel de Arca

In [1]:
import os
import json
import numpy as np
import requests
import pandas as pd
from dotenv import load_dotenv

## Abrir tablas y filtrar datos

In [3]:
load_dotenv()
config = json.load(open('../config/config.json'))
simbolos_tabla = '../datos/entrada/csv/Simbolos_2_registros.csv'
simbolos = pd.read_csv(simbolos_tabla, dtype=str)
simbolos = simbolos.dropna(how='all')
simbolos = simbolos.dropna(subset=['id'])
simbolos['id'] = simbolos['id'].astype(int)
simbolos = simbolos.sort_values(by='id')

filtrar = False

if filtrar:
    obras_tabla = '../datos/salida/obra.csv'

    # dataframes de las tablas
    obras = pd.read_csv(obras_tabla, dtype=str)
    #filtrar los simbolos por los ids de obras en arca
    simbolos_filtrados = simbolos.loc[simbolos['artwork_id'].isin(obras['arca_id']).tolist()]
    simbolos = simbolos_filtrados
    #muestra para prueba
    #simbolos_filtrados = simbolos_filtrados.sample(1)
    #len(simbolos_filtrados.index)
    #simbolos_filtrados

simbolos

id artwork_id artwork_symbol_id
13729       1       2307                 1
23164       2       3904                 1
33943       4       5832                 2
33851       5       5815                 2
33639       6       5786                 4
...       ...        ...               ...
99009  134950      20920               365
99083  134951      20972               365
96488  134952      19660               365
78415  134953      15373               365
96655  134954      19773               365

[99086 rows x 3 columns]

## URLS

In [4]:
#baseurl = 'http://localhost:8055/'
baseurl = config['baseurl']
obra_simbolos_baseurl = f'{baseurl}items/obra_simbolos_lista'
obras_url = f'{baseurl}items/obra'
simbolos_url = f'{baseurl}items/simbolos_lista'

key = os.getenv('KEY')
headers =  {'Authorization':f'Bearer {key}'}


## Iteración

In [14]:
for index, row in simbolos.iterrows():
    m2m_arcaid  = row['id']
    obra_arcaID = row['artwork_id']
    simbolo_arcaID = row['artwork_symbol_id']
    obra_url = f'{obras_url}?filter[arca_id][_eq]={obra_arcaID}&limit=1'
    sim_url = f'{simbolos_url}?filter[arca_id][_eq]={simbolo_arcaID}&limit=1'
    #obra = {}
    #simbolo = {}

    #obtener la obra de la api
    try:
        r_obra = requests.get(obra_url)
        r_obra.raise_for_status()
        print(f'econtrada obra: {obra_arcaID}')
    except requests.RequestException as err:
        print(f'Error obteniendo obra: {obra_arcaID}')
        print(err)
        # si se produce error, continua el siguiente registro
        continue

    #se obtienen los datos de la respuesta
    try:
        obra = r_obra.json()['data'][0]
        #print(obra)
    except IndexError as e:
        print(e)
        continue

    #obtener el simbolo de la api
    try: 
        r_sim = requests.get(sim_url)
        r_sim.raise_for_status()
    except requests.RequestException as err:
        print(f'Error obteniendo simbolo: {simbolo_arcaID}')
        print(err)
        continue

    #se obtienen los datos de la respuesta
    try:
        simbolo = r_sim.json()['data'][0]
        #print(simbolo)
    except IndexError as e:
        print(e)
        continue

    # crear el objeto obra simbolo con los ids de los objetos viculados
    obra_sim = {}
    obra_sim['arca_id'] = m2m_arcaid 
    obra_sim['obra_id'] = obra['id']
    obra_sim['simbolos_lista_id'] = simbolo['id']
    
    # crear m2m obra simbolo
    try:
        r_obsim_m2m = requests.post(obra_simbolos_baseurl, json = obra_sim, headers=headers)
        r_obsim_m2m.raise_for_status()
    except requests.RequestException as err:
        print(f'Error creando m2m obra simbolo: {obra_sim}')
        print(err)
        continue

    obsim_m2m = r_obsim_m2m.json()['data']
    m2mid = obsim_m2m['id']
    print(f'Creada relacion obra simbolo: {m2mid} arcaid: {m2m_arcaid}')
    #print(obsim_m2m)
    

econtrada obra: 2307
Creada relacion obra simbolo: 10665 arcaid: 1
econtrada obra: 3904
Creada relacion obra simbolo: 10666 arcaid: 2
econtrada obra: 5832
Creada relacion obra simbolo: 10667 arcaid: 4
econtrada obra: 5815
Creada relacion obra simbolo: 10668 arcaid: 5
econtrada obra: 5786
Creada relacion obra simbolo: 10669 arcaid: 6
econtrada obra: 5829
Creada relacion obra simbolo: 10670 arcaid: 7
econtrada obra: 2931
Creada relacion obra simbolo: 10671 arcaid: 8
econtrada obra: 1488
Creada relacion obra simbolo: 10672 arcaid: 9
econtrada obra: 4517
Creada relacion obra simbolo: 10673 arcaid: 10
econtrada obra: 3632
Creada relacion obra simbolo: 10674 arcaid: 11
econtrada obra: 3342
Creada relacion obra simbolo: 10675 arcaid: 13
econtrada obra: 5831
Creada relacion obra simbolo: 10676 arcaid: 15
econtrada obra: 5818
Creada relacion obra simbolo: 10677 arcaid: 16
econtrada obra: 4671
Creada relacion obra simbolo: 10678 arcaid: 17
econtrada obra: 2741
Creada relacion obra simbolo: 10679